# Separating Out Beats

In [1]:
using CSV, Plots, Images #, TimeSeries
using StatsBase
using Interact
plotlyjs()

Plots.PlotlyJSBackend()

These are all separate files I wrote to handle chunks of the process that are rather mundane.

In [2]:
include("findpeaks.jl")
include("pan_tompkins.jl")
include("run_pan_tompkins.jl")

run_pan_tompkins (generic function with 1 method)

Run Pan-Tompkins on a chunk of arrhythmia data

In [3]:
fs_arrhyth = 360;
sample_arrhyth = CSV.read("207.csv",header = ["Time", "ECG1", "ECG2"], datarow=1, nullable=false)
fs = fs_arrhyth;
x = sample_arrhyth[360*1700:360*1730,3];
t = sample_arrhyth[360*1700:360*1730,1];

x_HP, x_MAF, qrs_i, qrs_c, SIGL_buf, NOISL_buf, THRS_buf, qrs_i_raw, qrs_amp_raw, SIGL_buf1, NOISL_buf1, THRS_buf1 = run_pan_tompkins(x,t,fs);

In [4]:
#Filtered signal
plot(t,x_HP,title = "Filtered Signal after Algorithm",xlabel="Time (sec)",label = "Filtered Signal")
plot!(t[qrs_i_raw],qrs_amp_raw,line = :scatter,label = "Identified Peaks") 
plot!(t[qrs_i_raw],SIGL_buf1,label = "Signal Level")
plot!(t[qrs_i_raw],NOISL_buf1, label = "Noise Level")
plot!(t[qrs_i_raw],THRS_buf1, label = "Threshold")

Separate into individual "beats" based on just breaking halfway in between successive peaks. 

In [5]:
#Separate based on halfway in between peaks
breaks = zeros(Int64,0);
breaks = append!(breaks,1)
for i = 1:length(qrs_i_raw)-1
    breaks = append!(breaks,round(0.5.*(qrs_i_raw[i] + qrs_i_raw[i+1])))    
end
breaks = append!(breaks,min(length(t),2*qrs_i_raw[end]-breaks[end]))
breaks[1] = max(1,2*qrs_i_raw[1]-breaks[2]);

In [6]:
plot(t,x_HP,title = "Filtered Signal after Algorithm",xlabel="Time (sec)")
plot!(t[qrs_i_raw],qrs_amp_raw,line = :scatter) 
plot!(t[breaks],line = :vline)

#### On full arrhythmia set from a single subject ####

Run Pan-Tompkins on the full dataset from a single subject.

In [7]:
#Test on arrhythmia sample
fs = fs_arrhyth;
x = sample_arrhyth[:,3];
t = sample_arrhyth[:,1];

x_HP, x_MAF, qrs_i, qrs_c, SIGL_buf, NOISL_buf, THRS_buf, qrs_i_raw, qrs_amp_raw, SIGL_buf1, NOISL_buf1, THRS_buf1 = run_pan_tompkins(x,t,fs);

In [8]:
include("get_breaks.jl")

get_breaks (generic function with 1 method)

Separate into individual beats as above and plot. 

In [9]:
breaks = get_breaks(t,qrs_i_raw);
length(breaks)

2156

In [10]:
@manipulate for n in 1:length(breaks)-1
    plot(t[breaks[n]:breaks[n+1]],x_HP[breaks[n]:breaks[n+1]],title = "Beat #$n")
    #plot!(t[qrs_i])
end

Interact.Options{:SelectionSlider,Any}(1: "input" = 1078 Any , "n", 1078, "1078", 1078, Interact.OptionDict(DataStructures.OrderedDict{Any,Any}("1"=>1,"2"=>2,"3"=>3,"4"=>4,"5"=>5,"6"=>6,"7"=>7,"8"=>8,"9"=>9,"10"=>10…), Dict{Any,Any}(Pair{Any,Any}(1704, "1704"),Pair{Any,Any}(1760, "1760"),Pair{Any,Any}(306, "306"),Pair{Any,Any}(1316, "1316"),Pair{Any,Any}(1090, "1090"),Pair{Any,Any}(2111, "2111"),Pair{Any,Any}(1333, "1333"),Pair{Any,Any}(29, "29"),Pair{Any,Any}(1671, "1671"),Pair{Any,Any}(1131, "1131")…)), Any[], Any[], true, "horizontal")